# Notifications API (`.notifications`)

Estimated reading time: 5'

## What you'll learn

This guide presents how notifications work and can be enabled in PySyft. 

## Introduction

PySyft allows for responsible access to sensitive data. The nature of this kind of work is that often there will be processes may need external review, or need to happen asychronously. For instance, if a Data Scientist submits some code they'd like to be run against private data, often there will be a Data Owner who will want to manually review that code, before sending a response back.

However - how would the Data Owner know when a code request has been submitted? And how would the Data Scientist know when a response has been returned?

These kinds of scenarios that motivates the existance of notifications to PySyft. Currently we support only email notifications,thus in the rest of the guide, `notification` refers to an `email notification`, and these terms may be used interchangeably.


```{admonition} Email Notifications
An `Email Notification` alerts either the Data Scientist or the Data Owner of an event occuring. The events that trigger email notifications can be toggled. The e-mail protocol that PySyft currently supports is the `Simple Mail Transfer Protocol`, or `SMTP`. You can use a service like [SendGrid](https://sendgrid.com/en-us) to setup and create an STMP token for use with PySyft.
```



### How it works

It is pretty simple to set up notifications:
- **Prerequisite**: Data Owner setups at the SMTP credentials on the server
- Data Owner enables the dispatch of notifications at a server-level
- Any user of the server, data owner or data scientists configure the **client** to receive email notifications, or can deactivate them

It is helpful to remember that email notifications are designed to be primarily carried out on the **low side** server.

### What notifications are dispatched?

Currently, only the most important notifications are dispatched by the system. These are:
- When new users sign up (admins)
- When requests are submitted (admins)
- When requests change state (data scientists)

This allows both parties to be efficient working async by knowing when something is pending their input.

## Setup SMTP credentials

To setup the SMTP credentials, one can specify them either at deployment (A) using proper secrets in both single container or k8s mode, but as well after the node is deployed (B).

The main parameteres to pass are:
- `username`: Whatever name you'd like to give for this set of credentials.
- `password`: The SMTP token. You can generate one using a service like SendGrid!
- `sender`: The email you want the notifications to be sent from

Below you see detailed documentation on what you should to pass these.

### A. During deployment

#### Single-container

The deployment using the single container uses multiple `.yaml` files during the deployment. These can be updated directly before doing the docker deployment. You can find them in the `backend-statefulset.yaml` as such:
```yaml
# SMTP
- name: SMTP_HOST
    value: {{ .Values.node.smtp.host | quote }}
- name: SMTP_PORT
    value: {{ .Values.node.smtp.port | quote }}
- name: SMTP_USERNAME
    value: {{ .Values.node.smtp.username | quote }}
- name: SMTP_PASSWORD
    {{- if .Values.node.smtp.existingSecret }}
    valueFrom:
    secretKeyRef:
        name: {{ .Values.node.smtp.existingSecret }}
        key: smtpPassword
    {{ else }}
    value: {{ .Values.node.smtp.password | quote }}
    {{ end }}
- name: EMAIL_SENDER
    value: {{ .Values.node.smtp.from | quote}}
```

To secure your SMTP token, we recommend you to use [Docker secrets](https://docs.docker.com/engine/swarm/secrets/).

#### Kubernetes via Helm

To specify the necessary credentials, you can update the default `values.yaml` values with yours. If you inspect it, you will find the following section which describes the SMTP settings.

```yaml
# SMTP Settings
smtp:
  # Existing secret for SMTP with key 'smtpPassword'
  existingSecret: null
  host: smtp.sendgrid.net
  port: 587
  from: noreply@openmined.org
  username: apikey
  password: password
```

These can be updated via the `helm` operations. For more detailes, please look at [the deployment in k8s guide](../deployment/deployment-doc-5-0-deploy-k8s).

### B. Using the Python client

To show how email notifications can be setup and configured, we will launch now a test server for our purpose and login into it using default credentials.

In [ ]:
import syft as sy

In [ ]:
server = sy.orchestra.launch(name="test_server", port="auto", dev_mode=False, reset=True)

# logging in with default credentials
client = sy.login(email="info@openmined.org", password="changethis", port=server.port)

To do this, we'll have to specify three fields:

- `email_username`: Whatever name you'd like to give for this set of credentials.
- `email_password`: The SMTP token. You can generate one using a service like SendGrid!
- `email_sender`: The email you want the notifications to be sent from, e.g. noreply@specialorg.org
- `email_server`: The SMTP server address 
- `email_port`: The port where the SMTP is accesible

Note that all start with `email` since we are working with email notifications. We are working to support more notifications formats!

```python
client.settings.enable_notifications(
    email_username="..", 
    email_password="..", 
    email_sender="..", 
    email_server="..", 
    email_port="..")
```

## Enable server notifications

Data Owner can check the current server settings as:

In [ ]:
client.notifications.settings()

To update them to enable or disable notifications, we can update the settings as:

In [ ]:
client.settings.disable_notifications()

In [ ]:
client.settings.enable_notifications()


## Activate notifications as an user

To start receiving notifications for the events happening on the server that could be of interest to you, you can simply do:

In [ ]:
client.notifications.activate()

To see the current status of your notifications, you can look into `client.account`, which gives an overview of your account:

In [ ]:
client.account.notifications_enabled


We are working to offer support for further notifications system, but enabling notifications via SMS or Slack is not yet possible.
In case you would like to stop receiving the notifications, please proceed with:

In [ ]:
client.notifications.deactivate()
